<a href="https://colab.research.google.com/github/s0ku00/DTS/blob/main/Support_Vector_Machines.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [39]:
import pandas as pd
from sklearn.preprocessing import OneHotEncoder
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.svm import SVR
from sklearn.metrics import mean_squared_error,  r2_score

data = pd.read_csv('/content/Electric_cars_dataset.csv')

data.head(10)
print(data.dtypes)

ID                                                    object
VIN (1-10)                                            object
County                                                object
City                                                  object
State                                                 object
ZIP Code                                             float64
Model Year                                           float64
Make                                                  object
Model                                                 object
Electric Vehicle Type                                 object
Clean Alternative Fuel Vehicle (CAFV) Eligibility     object
Electric Range                                         int64
Base MSRP                                              int64
Legislative District                                 float64
DOL Vehicle ID                                         int64
Vehicle Location                                      object
Electric Utility        

<ipython-input-39-16258d78e1cb>:8: DtypeWarning: Columns (17) have mixed types. Specify dtype option on import or set low_memory=False.
  data = pd.read_csv('/content/Electric_cars_dataset.csv')


In [26]:
missing_values = data.isnull().sum()
print(missing_values)

ID                                                     0
VIN (1-10)                                             0
County                                                 4
City                                                  10
State                                                 11
ZIP Code                                               7
Model Year                                             7
Make                                                   4
Model                                                 14
Electric Vehicle Type                                  0
Clean Alternative Fuel Vehicle (CAFV) Eligibility      0
Electric Range                                         0
Base MSRP                                              0
Legislative District                                 173
DOL Vehicle ID                                         0
Vehicle Location                                     541
Electric Utility                                     766
Expected Price ($1k)           

In [31]:
# Fill missing values for categorical columns with 'missing'
categorical_features = ['VIN (1-10)', 'County', 'City', 'State', 'Make', 'Model', 'Electric Vehicle Type', 'Clean Alternative Fuel Vehicle (CAFV) Eligibility', 'Vehicle Location', 'Electric Utility', 'Expected Price ($1k)']
for col in categorical_features:
    data[col].fillna('missing', inplace=True)

# Fill missing values for numerical columns with the mean
numerical_features = ['Legislative District']
for col in numerical_features:
    data[col].fillna(data[col].mean(), inplace=True)

# Drop rows where 'Model Year' has NaN values
ecd_dataset = data.dropna()

ecd_dataset.isnull().sum()

ID                                                   0
VIN (1-10)                                           0
County                                               0
City                                                 0
State                                                0
ZIP Code                                             0
Model Year                                           0
Make                                                 0
Model                                                0
Electric Vehicle Type                                0
Clean Alternative Fuel Vehicle (CAFV) Eligibility    0
Electric Range                                       0
Base MSRP                                            0
Legislative District                                 0
DOL Vehicle ID                                       0
Vehicle Location                                     0
Electric Utility                                     0
Expected Price ($1k)                                 0
dtype: int

In [ ]:
!pip install pandas-profiling

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 324.4/324.4 kB 5.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 359.5/359.5 kB 23.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 104.8/104.8 kB 12.2 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 686.1/686.1 kB 38.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 296.5/296.5 kB 22.0 MB/s eta 0:00:00
  Created wheel for htmlmin: filename=htmlmin-0.1.12-py3-none-any.whl size=27080 sha256=9c696745525c4dffb9af534ddf607c00af23babdaeae3efeffbfbd71f77a61b5
  Stored in directory: /root/.cache/pip/wheels/dd/91/29/a79cecb328d01739e64017b6fb9a1ab9d8cb1853098ec5966d
Successfully built htmlmin


In [ ]:
from ydata_profiling import ProfileReport

profile = ProfileReport(ecd_dataset, title='Electric Cars Profiling Report')

profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [36]:
# Ensure all values in 'Expected Price ($1k)' are numeric
ecd_dataset['Expected Price ($1k)'] = pd.to_numeric(ecd_dataset['Expected Price ($1k)'], errors='coerce')

# Remove rows with missing values in 'Expected Price ($1k)'
ecd_dataset = ecd_dataset.dropna(subset=['Expected Price ($1k)'])

# Identify outliers using IQR
Q1 = ecd_dataset['Expected Price ($1k)'].quantile(0.25)
Q3 = ecd_dataset['Expected Price ($1k)'].quantile(0.75)
IQR = Q3 - Q1

# Define outliers as points that fall below Q1 - 1.5 * IQR or above Q3 + 1.5 * IQR
outliers = (ecd_dataset['Expected Price ($1k)'] < (Q1 - 1.5 * IQR)) | (ecd_dataset['Expected Price ($1k)'] > (Q3 + 1.5 * IQR))

# Filter out the outliers
ecd_dataset = ecd_dataset[~outliers]

In [40]:
# Define features and target variable
features = [col for col in ecd_dataset.columns if col not in ['ID', 'VIN (1-10)', 'County', 'City', 'State', 'ZIP Code', 'Electric Vehicle Type', 'Clean Alternative Fuel Vehicle (CAFV) Eligibility', 'Electric Range', 'Base MSRP', 'Legislative District', 'DOL Vehicle ID', 'Vehicle Location', 'Electric Utility', 'Expected Price ($1k)']]
target = 'Expected Price ($1k)'

# Define the features and the target
X = ecd_dataset[features]
y = ecd_dataset[target]

# Splitting into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# Scaling numerical features (if necessary)
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)

# SVM model
svm_model = SVR(kernel='rbf')  # Use RBF kernel for SVM regression

# Train the SVR model
svm_model.fit(X_train_scaled, y_train)

# Predict
y_pred = svm_model.predict(X_test_scaled)

# Evaluate the model
mse = mean_squared_error(y_test, y_pred)
r2 = r2_score(y_test, y_pred)

In [41]:
print(f"Mean Squared Error: {mse}")
print(f"R^2 Score: {r2}")

Mean Squared Error: 53.60210838514308
R^2 Score: 0.8987570045437461


In [ ]:
'''
MSE = 53.6021: The mean squared error (MSE) measures the average squared difference between the predicted and actual values.
              This suggests that, on average, the model's predictions are off by approximately 53.6021 units squared.
R^2 Score = 0.8988: This indicates that the model explains approximately 89.88% of the variance in the dependent variable.
                    In other words, the model fits the data quite well, explaining a high percentage of the variability.
'''